In [17]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import Image
from sklearn.tree import export_graphviz
import pydotplus

In [18]:
data = pd.read_csv("datasets/winequality-red.csv")

In [19]:
data.head(3)

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   

   alcohol  quality  
0      9.4        5  
1      9.8        5  
2      9.8        5

In [20]:
classes = data['quality'].unique()
np.sort(classes)
classes

array([5, 6, 7, 4, 8, 3], dtype=int64)

In [21]:
x = data.iloc[:,:-1]
y = data.iloc[:,-1]

In [31]:
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier

from sklearn.preprocessing import StandardScaler
x_transform = StandardScaler().fit_transform(x)

In [23]:
x_train,x_test,y_train,y_test = train_test_split(x_transform,y,test_size=0.2,random_state=40)

In [24]:
clf = DecisionTreeClassifier()
clf.fit(x_train,y_train)

DecisionTreeClassifier()

In [25]:
clf.score(x_test,y_test)

0.653125

In [26]:
feature_names = list(x.columns)
class_labels = list(y.unique())
class_labels

[5, 6, 7, 4, 8, 3]

### Visualize Decision Tree

In [27]:
import os
os.environ["PATH"] += os.pathsep + 'C:\Program Files (x86)\Graphviz2.38/bin/'

In [32]:
dot_data = export_graphviz(clf,feature_names=feature_names,rounded=True,filled=True)

graph = pydotplus.graph_from_dot_data(dot_data)
graph.write_png("PrePruned_Tree_new.png")

Image(graph.create_png())

### PCA

In [29]:
# scale data
from sklearn.preprocessing import StandardScaler
x_transform = StandardScaler().fit_transform(x)

In [30]:
from sklearn.decomposition import PCA
principalComps = PCA().fit_transform(x_transform)
plt.figure()
plt.plot(np.cumsum(pca.explained_variance_ratio_))
plt.xlabel("No of components")
plt.ylabel("Variance %")

NameError: name 'pca' is not defined

<Figure size 432x288 with 0 Axes>

It shows that 8 features can explain upto 95% of the variance in the dataset

In [ ]:
## pick best 8 columns
new_data = PCA(n_components=8).fit_transform(x_transform)
x_pca = pd.DataFrame(new_data,columns=['PC1','PC2','PC3','PC4','PC5','PC6','PC7','PC8'])
x_pca.head()

In [ ]:
x_train,x_test,y_train,y_test = train_test_split(x_pca,y,test_size=0.2,random_state=40)
clf = DecisionTreeClassifier()
clf.fit(x_train,y_train)
clf.score(x_test,y_test)

### Hyper Parameter Tuning : GridSearchCV Algorithm
#### Computationally Very Expensive

In [61]:
# hyper paramater tuning for 3 hyperparameters
grid_param = {
    'criterion' : ['gini', 'entrophy'],
    'max_depth' : range(2,32,1),
    'min_samples_leaf' : range(1,10,1),
    'min_samples_split' : range(2,10,1),
    'splitter' : ['best','random']
}

In [62]:
from sklearn.model_selection import GridSearchCV
grid_search = GridSearchCV(estimator=clf,
                           param_grid=grid_param,
                          cv=5,
                          n_jobs=-1)

In [66]:
grid_search.fit(x_transform,y_train)

ValueError: Found input variables with inconsistent numbers of samples: [1599, 1279]

#### Gives best parameters which you can use

In [60]:
best_params = grid_search.best_params_
best_params

{'criterion': 'gini',
 'max_depth': 8,
 'min_samples_leaf': 1,
 'min_samples_split': 2,
 'splitter': 'random'}

In [65]:
grid_search.best_score_

0.5728683385579937

### Cross Validation